## idmapping UniProt

In [11]:
#https://ftp.uniprot.org/pub/databases/uniprot/current_release/knowledgebase/idmapping/README
#https://ftp.uniprot.org/pub/databases/uniprot/current_release/knowledgebase/idmapping/README
path = '../data/UniProt'

In [2]:
import os
import csv
import io
import gzip

In [3]:
def generate_idmapping(path):
    """Returns a generator of idmapping.dat.gz rows."""
    read_file = gzip.open(path, 'rb')
    text = io.TextIOWrapper(read_file)
    reader = csv.reader(text, delimiter='\t')
    for row in reader:
        yield row
    read_file.close()

In [4]:
mapping_generator = generate_idmapping(os.path.join(path, 'idmapping.dat.gz'))

In [5]:
extract = {'GeneID', 'HGNC'}
mappings = {target: set() for target in extract}

for accession, target, target_id in mapping_generator:
    if target not in extract:
        continue
    mappings[target].add((accession, target_id))

In [12]:
for target, mapset in mappings.items():
    write_file = gzip.open(os.path.join(path, '{}.tsv.gz'.format(target)), 'wb')
    wrapper = io.TextIOWrapper(write_file)
    writer = csv.writer(wrapper, delimiter='\t')
    writer.writerow(['uniprot', target])
    writer.writerows(sorted(mapset))
    write_file.close()

## Process EntrezGene

In [1]:
import os
import gzip
import re
import json

import pandas

In [4]:
# Read Entrez info dataset
path = '../data/EntrezGene'

with gzip.open(os.path.join(path, 'Homo_sapiens.gene_info.gz'), 'rt') as read_file:
    #matches = re.match(r'#Format: (.+) \(', next(read_file))
    #columns = matches.group(1).split(' ')
    #gene_df = pandas.read_table(read_file, names = columns, na_values=['-'])
    gene_df = pandas.read_table(read_file, na_values=['-'])
    gene_df = gene_df.rename(columns={'#tax_id':'tax_id'})

# Restrict to homo sapiens
gene_df = gene_df.query('tax_id == 9606')

len(gene_df)

/var/folders/sg/983t9lp12bsfyjv9ylh6002m0000gt/T/ipykernel_9220/734070155.py:8: DtypeWarning: Columns (4,15) have mixed types. Specify dtype option on import or set low_memory=False.
  gene_df = pandas.read_table(read_file, na_values=['-'])


193382

In [5]:
# save a select columnset
columns = ['tax_id', 'GeneID', 'Symbol', 'chromosome', 'map_location', 'type_of_gene', 'description']
select_df = gene_df[columns]
select_df.to_csv(os.path.join(path, 'genes-human.tsv'), sep='\t', index=False)
select_df.head()

tax_id  GeneID Symbol chromosome map_location    type_of_gene  \
0    9606       1   A1BG         19     19q13.43  protein-coding   
1    9606       2    A2M         12     12p13.31  protein-coding   
2    9606       3  A2MP1         12     12p13.31          pseudo   
3    9606       9   NAT1          8         8p22  protein-coding   
4    9606      10   NAT2          8         8p22  protein-coding   

                          description  
0              alpha-1-B glycoprotein  
1               alpha-2-macroglobulin  
2  alpha-2-macroglobulin pseudogene 1  
3               N-acetyltransferase 1  
4               N-acetyltransferase 2

## Parse the DrugBank XML and extract TSVs

In [1]:
import os
import csv
import gzip
import collections
import re
import io
import json
import xml.etree.ElementTree as ET

import requests
import pandas

In [2]:
path = '../data/DrugBank'
xml_file = os.path.join(path, 'full database.xml') 
tree = ET.parse(xml_file)
root = tree.getroot()

In [8]:
ns = '{http://www.drugbank.ca}'
inchikey_template = "{ns}calculated-properties/{ns}property[{ns}kind='InChIKey']/{ns}value"
inchi_template = "{ns}calculated-properties/{ns}property[{ns}kind='InChI']/{ns}value"

rows = list()
for i, drug in enumerate(root):
    row = collections.OrderedDict()
    assert drug.tag == ns + 'drug'
    row['type'] = drug.get('type')
    row['drugbank_id'] = drug.findtext(ns + "drugbank-id[@primary='true']")
    row['name'] = drug.findtext(ns + "name")
    row['description'] = drug.findtext(ns + "description")
    row['groups'] = [group.text for group in
        drug.findall("{ns}groups/{ns}group".format(ns = ns))]
    row['atc_codes'] = [code.get('code') for code in
        drug.findall("{ns}atc-codes/{ns}atc-code".format(ns = ns))]
    row['categories'] = [x.findtext(ns + 'category') for x in
        drug.findall("{ns}categories/{ns}category".format(ns = ns))]
    row['inchi'] = drug.findtext(inchi_template.format(ns = ns))
    row['inchikey'] = drug.findtext(inchikey_template.format(ns = ns))
    
    # Add drug aliases
    aliases = {
        elem.text for elem in 
        drug.findall("{ns}international-brands/{ns}international-brand".format(ns = ns)) +
        drug.findall("{ns}synonyms/{ns}synonym[@language='English']".format(ns = ns)) +
        drug.findall("{ns}international-brands/{ns}international-brand".format(ns = ns)) +
        drug.findall("{ns}products/{ns}product/{ns}name".format(ns = ns))

    }
    aliases.add(row['name'])
    row['aliases'] = sorted(aliases)

    rows.append(row)

In [9]:
#alias_dict = {row['drugbank_id']: row['aliases'] for row in rows}
#with open(os.path.join(path, 'aliases.json'), 'w') as fp:
#    json.dump(alias_dict, fp, indent=2, sort_keys=True)

In [10]:
def collapse_list_values(row):
    for key, value in row.items():
        if isinstance(value, list):
            row[key] = '|'.join(value)
    return row

rows = list(map(collapse_list_values, rows))

In [11]:
columns = ['drugbank_id', 'name', 'type', 'groups', 'atc_codes', 'categories', 'inchikey', 'inchi', 'description']
drugbank_df = pandas.DataFrame.from_dict(rows)[columns]
drugbank_df.head()

drugbank_id                 name     type                    groups  \
0     DB00001            Lepirudin  biotech        approved|withdrawn   
1     DB00002            Cetuximab  biotech                  approved   
2     DB00003         Dornase alfa  biotech                  approved   
3     DB00004  Denileukin diftitox  biotech  approved|investigational   
4     DB00005           Etanercept  biotech  approved|investigational   

  atc_codes                                         categories inchikey inchi  \
0   B01AE02  Amino Acids, Peptides, and Proteins|Anticoagul...     None  None   
1   L01FE01  Amino Acids, Peptides, and Proteins|Antibodies...     None  None   
2   R05CB13  Amino Acids, Peptides, and Proteins|Cough and ...     None  None   
3   L01XX29  ADP Ribose Transferases|Amino Acids, Peptides,...     None  None   
4   L04AB01  Agents reducing cytokine levels|Amino Acids, P...     None  None   

                                         description  
0  Lepirudin is a recombinant hirudin formed by 6...  
1  Cetuximab is a recombinant chimeric human/mous...  
2  Dornase alfa is a biosynthetic form of human d...  
3  A recombinant DNA-derived cytotoxic protein co...  
4  Dimeric fusion protein consisting of the extra...

In [12]:
drugbank_slim_df = drugbank_df[
    drugbank_df.groups.map(lambda x: 'approved' in x) &
    drugbank_df.inchi.map(lambda x: x is not None) &
    drugbank_df.type.map(lambda x: x == 'small molecule')
]
drugbank_slim_df.head()

drugbank_id          name            type                    groups  \
5      DB00006   Bivalirudin  small molecule  approved|investigational   
6      DB00007    Leuprolide  small molecule  approved|investigational   
13     DB00014     Goserelin  small molecule                  approved   
25     DB00027  Gramicidin D  small molecule                  approved   
33     DB00035  Desmopressin  small molecule                  approved   

          atc_codes                                         categories  \
5           B01AE06  Amino Acids, Peptides, and Proteins|Anticoagul...   
6   L02AE51|L02AE02  Adrenal Cortex Hormones|Agents Causing Muscle ...   
13          L02AE03  Adrenal Cortex Hormones|Amino Acids, Peptides,...   
25          R02AB30  Amino Acids, Peptides, and Proteins|Anti-Bacte...   
33          H01BA02  Agents that produce hypertension|Amino Acids, ...   

                       inchikey  \
5   OIRCOABEOLEUMC-GEJPAHFPSA-N   
6   GFIJNRVAKGFPGQ-LIJARHBVSA-N   
13  BLCLNMBMMGCOAS-URPVMXJPSA-N   
25  NDAYQJDHGXTBJL-MWWSRJDJSA-N   
33  NFLWUMRGJYTJIN-PNIOQBSNSA-N   

                                                inchi  \
5   InChI=1S/C98H138N24O33/c1-5-52(4)82(96(153)122...   
6   InChI=1S/C59H84N16O12/c1-6-63-57(86)48-14-10-2...   
13  InChI=1S/C59H84N18O14/c1-31(2)22-40(49(82)68-3...   
25  InChI=1S/C96H135N19O16/c1-50(2)36-71(105-79(11...   
33  InChI=1S/C46H64N14O12S2/c47-35(62)15-14-29-40(...   

                                          description  
5   Bivalirudin is a synthetic 20 residue peptide ...  
6   Leuprolide is a synthetic 9-residue peptide an...  
13  Goserelin is a synthetic hormone. In men, it s...  
25  Gramcidin D is a heterogeneous mixture of thre...  
33  Desmopressin (dDAVP), a synthetic analogue of ...

In [ ]:
# write drugbank tsv
drugbank_df.to_csv(os.path.join(path, 'drugbank.tsv'), sep='\t', index=False)

# write slim drugbank tsv
drugbank_slim_df.to_csv(os.path.join(path, 'drugbank-slim.tsv'), sep='\t', index=False)

In [4]:
protein_rows = list()
for i, drug in enumerate(root):
    drugbank_id = drug.findtext(ns + "drugbank-id[@primary='true']")
    for category in ['target', 'enzyme', 'carrier', 'transporter']:
        proteins = drug.findall('{ns}{cat}s/{ns}{cat}'.format(ns=ns, cat=category))
        for protein in proteins:
            row = {'drugbank_id': drugbank_id, 'category': category}
            row['organism'] = protein.findtext('{}organism'.format(ns))
            row['known_action'] = protein.findtext('{}known-action'.format(ns))
            actions = protein.findall('{ns}actions/{ns}action'.format(ns=ns))
            row['actions'] = '|'.join(action.text for action in actions)
            uniprot_ids = [polypep.text for polypep in protein.findall(
                "{ns}polypeptide/{ns}external-identifiers/{ns}external-identifier[{ns}resource='UniProtKB']/{ns}identifier".format(ns=ns))]            
            if len(uniprot_ids) != 1:
                continue
            row['uniprot_id'] = uniprot_ids[0]
            #ref_text = protein.findtext("{ns}references[@format='textile']".format(ns=ns))
            #pmids = re.findall(r'pubmed/([0-9]+)', ref_text)
            pmids = protein.findall("{ns}references/{ns}articles/{ns}article/{ns}pubmed-id".format(ns=ns)) #update to fit the latest version of drugbank xml
            row['pubmed_ids'] = '|'.join(str(pmid.text) for pmid in pmids)
            protein_rows.append(row)

protein_df = pandas.DataFrame.from_dict(protein_rows)

In [5]:
protein_df#[protein_df['pubmed_ids']=='']

drugbank_id category                           organism known_action  \
0         DB00001   target                             Humans          yes   
1         DB00002   target                             Humans          yes   
2         DB00002   target                             Humans      unknown   
3         DB00002   target                             Humans      unknown   
4         DB00002   target                             Humans      unknown   
...           ...      ...                                ...          ...   
28720     DB17992   target  Pediculus humanus subsp. corporis      unknown   
28721     DB18236   target                             Humans          yes   
28722     DB18704   target                             Humans          yes   
28723     DB18716   target             Pseudomonas aeruginosa          yes   
28724     DB18716   enzyme                             Humans      unknown   

          actions uniprot_id                                    pubmed_ids  
0       inhibitor     P00734  10505536|10912644|11055889|11467439|11807012  
1          binder     P00533                             11752352|15821783  
2          binder     O75015                                      16336752  
3          binder     P02745                                      32117299  
4          binder     P02746                                      32117299  
...           ...        ...                                           ...  
28720  antagonist     E0W492                                      33600484  
28721   inhibitor     Q07912                                      28609657  
28722  stimulator     Q99062                                                
28723   inhibitor     P37321                                                
28724   inhibitor     P05181                                                

[28725 rows x 7 columns]

In [14]:
# Read our uniprot to entrez_gene mapping
url = '../data/UniProt/GeneID.tsv.gz'
with gzip.open(url, 'rt') as read_file:
    uniprot_df = pandas.read_table(read_file)
    uniprot_df.rename(columns={'uniprot': 'uniprot_id', 'GeneID': 'entrez_gene_id'}, inplace=True)
uniprot_df.shape

# merge uniprot mapping with protein_df
entrez_df = protein_df.merge(uniprot_df, how='inner')

In [13]:
"""
#legacy
response = requests.get('http://git.dhimmel.com/uniprot/data/map/GeneID.tsv.gz', stream=True)
text = io.TextIOWrapper(gzip.GzipFile(fileobj=response.raw))
uniprot_df = pandas.read_table(text, engine='python')
uniprot_df.rename(columns={'uniprot': 'uniprot_id', 'GeneID': 'entrez_gene_id'}, inplace=True)
uniprot_df
# merge uniprot mapping with protein_df
entrez_df = protein_df.merge(uniprot_df, how='inner')
"""

uniprot_id  entrez_gene_id
0        A0A010PZJ8        19039206
1        A0A010PZK3        19039211
2        A0A010PZK7        19039216
3        A0A010PZK9        19039221
4        A0A010PZL3        19039226
...             ...             ...
6660567      X5KBI2        23373303
6660568      X5KBJ0        23373148
6660569      X5KBL1        23373174
6660570      X5KBL5        23373179
6660571      X5KBV7        23372097

[6660572 rows x 2 columns]

In [16]:
columns = ['drugbank_id', 'category', 'uniprot_id', 'entrez_gene_id', 'organism',
           'known_action', 'actions', 'pubmed_ids']
entrez_df = entrez_df[columns]
entrez_df.shape

(27391, 8)

In [17]:
entrez_df.to_csv(os.path.join(path, 'proteins.tsv'), sep='\t', index=False)

## Durg Central - Convert drug targets

In [1]:
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

In [2]:
import pandas

In [3]:
url = '../data/UniProt/GeneID.tsv.gz'
entrez_map_df = pandas.read_table(url, compression='gzip')
entrez_map_df.head(2)
entrez_map_df.shape

uniprot    GeneID
0  A0A009GNX9   9382146
1  A0A009GQ85  60755424

(13529311, 2)

In [4]:
url = '../DrugBank/drugbank-slim.tsv'
drugbank_df = pandas.read_table(url)
drugbank_df = drugbank_df[['drugbank_id', 'name']]
drugbank_df = drugbank_df.rename(columns={'name': 'drugbank_name'})
drugbank_df.head(2)
drugbank_df.shape

drugbank_id drugbank_name
0     DB00006   Bivalirudin
1     DB00007    Leuprolide

(2778, 2)

In [6]:
url = '../data/DrugCentral/identifiers.tsv'
id_df = pandas.read_table(url, sep=',')
id_df = id_df.query("id_type == 'DRUGBANK_ID'")[['struct_id', 'identifier']]
id_df = id_df.rename(columns={'identifier': 'drugbank_id', 'struct_id': 'DRUG_ID'})
drugbank_df = id_df.merge(drugbank_df)
drugbank_df.head(2)
drugbank_df.shape

DRUG_ID drugbank_id  drugbank_name
0     5392     DB11791     Capmatinib
1     5393     DB15685  Selpercatinib

(2674, 3)

In [19]:
"""
path = 'https://raw.githubusercontent.com/olegursu/drugtarget/9a6d84bed8650c6c507a2d3d786814c774568610/drug_target.tsv'
#'https://github.com/legursu/drugtarget/raw/9a6d84bed8650c6c507a2d3d786814c774568610/drug_target.tsv'
check_target_df = pandas.read_table(path)
#check_target_df['SOURCE'].unique()
check_target_df['REFERENCE_check'] = check_target_df['REFERENCE'].str[:20]
check_target_df[check_target_df['SOURCE'].isin(['CHEMBL'])]['REFERENCE_check'].unique()
"""

array(['https://www.ebi.ac.u'], dtype=object)

In [9]:
path = '../data/DrugCentral/drug.target.interaction.tsv'
target_df = pandas.read_table(path)
target_df = target_df.rename(columns={'STRUCT_ID': 'DRUG_ID', 'ACCESSION': 'UNIPROT', 'TARGET_CLASS': 'TARGET_FAMILY', 'ACT_SOURCE':'SOURCE', 'ACT_SOURCE_URL': 'REFERENCE'})
target_df = drugbank_df.merge(target_df)
target_df = target_df[['drugbank_id', 'drugbank_name', 'TARGET_NAME', 'TARGET_FAMILY', 'UNIPROT', 'ACTION_TYPE', 'SOURCE', 'REFERENCE']]
target_df.head(2)
target_df.shape

# Split multi-protein targets into many rows
s = target_df.UNIPROT.str.split('|').apply(pandas.Series, 1).stack()
s.index = s.index.droplevel(-1)
s.name ='uniprot'
del target_df['UNIPROT']
target_df = target_df.join(s)
target_df.head(2)
target_df.shape

target_df = entrez_map_df.merge(target_df)
del target_df['uniprot']

target_df['action'] = target_df['ACTION_TYPE'].str.lower()
del target_df['ACTION_TYPE']

target_df['pubmed_id'] = target_df.REFERENCE.str.extract('pubmed.*/([0-9]+)')

target_df = target_df.drop_duplicates()
target_df.head(2)
target_df.shape

drugbank_id  drugbank_name                        TARGET_NAME TARGET_FAMILY  \
0     DB11791     Capmatinib  Hepatocyte growth factor receptor        Kinase   
1     DB15685  Selpercatinib                    Aurora kinase B        Kinase   

  UNIPROT ACTION_TYPE                 SOURCE  \
0  P08581   INHIBITOR  SCIENTIFIC LITERATURE   
1  Q96GD4   INHIBITOR             DRUG LABEL   

                                           REFERENCE  
0           https://pubmed.ncbi.nlm.nih.gov/21918175  
1  https://www.accessdata.fda.gov/drugsatfda_docs...

(16823, 8)

drugbank_id  drugbank_name                        TARGET_NAME TARGET_FAMILY  \
0     DB11791     Capmatinib  Hepatocyte growth factor receptor        Kinase   
1     DB15685  Selpercatinib                    Aurora kinase B        Kinase   

  ACTION_TYPE                 SOURCE  \
0   INHIBITOR  SCIENTIFIC LITERATURE   
1   INHIBITOR             DRUG LABEL   

                                           REFERENCE uniprot  
0           https://pubmed.ncbi.nlm.nih.gov/21918175  P08581  
1  https://www.accessdata.fda.gov/drugsatfda_docs...  Q96GD4

(19981, 8)

GeneID drugbank_id  drugbank_name                     TARGET_NAME  \
0    125206     DB09038  Empagliflozin  Sodium/glucose cotransporter 5   
1  66738197     DB01051     Novobiocin          DNULL gyrase subunit B   

  TARGET_FAMILY                 SOURCE  \
0   Transporter  SCIENTIFIC LITERATURE   
1        Enzyme                 CHEMBL   

                                  REFERENCE action pubmed_id  
0  https://pubmed.ncbi.nlm.nih.gov/21985634    NaN  21985634  
1                                       NaN    NaN       NaN

(18579, 9)

In [10]:
target_df[target_df['drugbank_id'].isin(['DB11791','DB15685'])]

GeneID drugbank_id  drugbank_name  \
2809     5979     DB15685  Selpercatinib   
3397     4233     DB11791     Capmatinib   
17261    9212     DB15685  Selpercatinib   

                                             TARGET_NAME TARGET_FAMILY  \
2809   Proto-oncogene tyrosine-protein kinase recepto...        Kinase   
3397                   Hepatocyte growth factor receptor        Kinase   
17261                                    Aurora kinase B        Kinase   

                      SOURCE  \
2809              DRUG LABEL   
3397   SCIENTIFIC LITERATURE   
17261             DRUG LABEL   

                                               REFERENCE     action pubmed_id  
2809   https://www.accessdata.fda.gov/drugsatfda_docs...  inhibitor       NaN  
3397            https://pubmed.ncbi.nlm.nih.gov/21918175  inhibitor  21918175  
17261  https://www.accessdata.fda.gov/drugsatfda_docs...  inhibitor       NaN

In [11]:
target_df['SOURCE'].unique()

array(['SCIENTIFIC LITERATURE', 'CHEMBL', 'WOMBAT-PK', 'DRUG MATRIX',
       'DRUG LABEL', 'IUPHAR', 'PDSP', 'DRUGBANK', 'KEGG DRUG', 'UNKNOWN'],
      dtype=object)

In [12]:
#https://think-lab.github.io/d/186/
#https://www.ncbi.nlm.nih.gov/pmc/articles/PMC10692006/
#DrugCentral contains 20,658 activity endpoints (drug-target pairs) for 2715 drugs across 3171 targets. Bioactivities are compiled from various sources: ChEMBLdb [24] (59.7%), WOMBAT-PK [25] (13.8%), DrugMatrix [26] (11.0%), IUPHAR/BPS Guide to Pharmacology [27] (6.1%), scientific literature (3.7%), PDSP [28] (3.6%), and drug labels (1.6%) (Table ​(Table3).3). 
target_source_map = {
    'CHEMBL': 'DrugCentral (ChEMBL)',
    'SCIENTIFIC LITERATURE': 'DrugCentral (literature)',
    'DRUG LABEL': 'DrugCentral (label)',
    'IUPHAR': 'DrugCentral (IUPHAR)',
    'KEGG DRUG': 'DrugCentral (KEGG DRUG)',
    'WOMBAT-PK': 'DrugCentral (WOMBAT-PK)',
    'DRUG MATRIX': 'DrugCentral (DrugMatrix)',
    'PDSP': 'DrugCentral (PDSP)',
    'DRUGBANK': 'DrugCentral (DrugBank)',
    'UNKNOWN': 'DrugCentral (unknown)',
}
target_df.SOURCE = target_df.SOURCE.map(target_source_map)
target_df.SOURCE.value_counts()
target_df.head(2)
target_df.shape

DrugCentral (ChEMBL)        11249
DrugCentral (WOMBAT-PK)      2876
DrugCentral (DrugMatrix)     2060
DrugCentral (IUPHAR)          944
DrugCentral (literature)      627
DrugCentral (PDSP)            589
DrugCentral (label)           135
DrugCentral (DrugBank)         67
DrugCentral (unknown)          23
DrugCentral (KEGG DRUG)         9
Name: SOURCE, dtype: int64

GeneID drugbank_id  drugbank_name                     TARGET_NAME  \
0    125206     DB09038  Empagliflozin  Sodium/glucose cotransporter 5   
1  66738197     DB01051     Novobiocin          DNULL gyrase subunit B   

  TARGET_FAMILY                    SOURCE  \
0   Transporter  DrugCentral (literature)   
1        Enzyme      DrugCentral (ChEMBL)   

                                  REFERENCE action pubmed_id  
0  https://pubmed.ncbi.nlm.nih.gov/21985634    NaN  21985634  
1                                       NaN    NaN       NaN

(18579, 9)

In [13]:
def condense_targets(df):
    """Condense drug-target relationships."""
    row = pandas.Series()
    row['pubmed_ids'] = '|'.join(sorted(df.pubmed_id.dropna().unique()))
    row['sources'] = '|'.join(sorted(df.SOURCE.dropna().unique()))
    row['actions'] = '|'.join(sorted(df.action.dropna().unique()))
    row['urls'] = '|'.join(sorted(url for url in df.REFERENCE.dropna().unique() if not 'pubmed' in url))
    return row
    
target_df = target_df.groupby(['GeneID', 'drugbank_id', 'drugbank_name']).apply(condense_targets).reset_index()

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

/var/folders/sg/983t9lp12bsfyjv9ylh6002m0000gt/T/ipykernel_7307/303211146.py:3: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  row = pandas.Series()
/var/folders/sg/983t9lp12bsfyjv9ylh6002m0000gt/T/ipykernel_7307/303211146.py:3: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  row = pandas.Series()
/var/folders/sg/983t9lp12bsfyjv9ylh6002m0000gt/T/ipykernel_7307/303211146.py:3: FutureWarning: The default dtype for empty Series will be 'obj

In [14]:
target_df

GeneID drugbank_id       drugbank_name pubmed_ids  \
0             18     DB01080          Vigabatrin              
1             19     DB01599            Probucol              
2             25     DB00317           Gefitinib              
3             25     DB00398           Sorafenib              
4             25     DB00530           Erlotinib              
...          ...         ...                 ...        ...   
17704  106821730     DB11828           Neratinib              
17705  106821730     DB12500          Fedratinib              
17706  107364480     DB00431             Lindane              
17707  107791137     DB00936      Salicylic acid              
17708  107791137     DB14006  Choline salicylate              

                       sources                        actions urls  
0         DrugCentral (ChEMBL)                      inhibitor       
1         DrugCentral (ChEMBL)                      inhibitor       
2         DrugCentral (ChEMBL)                                      
3         DrugCentral (ChEMBL)                                      
4         DrugCentral (ChEMBL)                                      
...                        ...                            ...  ...  
17704     DrugCentral (ChEMBL)                                      
17705     DrugCentral (ChEMBL)                                      
17706     DrugCentral (ChEMBL)  negative allosteric modulator       
17707  DrugCentral (WOMBAT-PK)                                      
17708  DrugCentral (WOMBAT-PK)                                      

[17709 rows x 7 columns]

In [18]:
import os
path = '../data/DrugCentral' 
target_df.to_csv(os.path.join(path, 'targets.tsv'), sep='\t', index=False)

## Unichem Map - Drugbank to BindingDB

In [1]:
import os
import csv
import collections
import json
import gzip
import io

import requests

In [2]:
path = '../data/DrugBank'

with open(os.path.join(path, 'drugbank.tsv')) as read_file:
    reader = csv.DictReader(read_file, delimiter='\t')
    drugbank = list(reader)

drugbank_ids = [drug['drugbank_id'] for drug in drugbank]
assert len(drugbank_ids) == len(set(drugbank_ids))

In [3]:
# Compound has InChIKey
collections.Counter(bool(drug['inchikey']) for drug in drugbank)

Counter({False: 4653, True: 11928})

In [4]:
# Compound types
collections.Counter(drug['type'] for drug in drugbank)

Counter({'biotech': 3882, 'small molecule': 12699})

In [5]:
id_to_source = {
    0: None,
    1: 'chembl',
    2: 'drugbank',
    3: 'pdb',
    4: 'iuphar',
    5: 'pubchem_dotf',
    6: 'kegg_ligand',
    7: 'chebi',
    8: 'nih_ncc',
    9: 'zinc',
    10: 'emolecules',
    11: 'ibm',
    12: 'atlas',
    13: 'ibm_patents',
    14: 'fdasrs',
    15: 'surechembl',
    17: 'pharmgkb',
    18: 'hmdb',
    20: 'selleck',
    21: 'pubchem_tpharma',
    22: 'pubchem',
    23: 'mcule',
    24: 'nmrshiftdb2',
    25: 'lincs',
    26: 'actor',
    27: 'recon',
    28: 'molport',
    29: 'nikkaji',
    31: 'bindingdb',
}

source_to_id = {v: k for k, v in id_to_source.items()}

In [6]:
#'https://www.ebi.ac.uk/unichem/rest/cpd_search/DB00006/2/0/0/4/0/0/0/0/1'
def connectivity_query(search_url, target = None, B = 0, C = 0, D = 0, E = 0, F = 0, G = 0):
    """
    https://www.ebi.ac.uk/unichem/info/widesearchInfo
    """
    url = '{search_url}/{A}/{B}/{C}/{D}/{E}/{F}/{G}/{H}'.format(
        search_url = search_url,
        A = source_to_id[target], # Sources
        B = B, # Pattern
        C = C, # Component Mapping
        D = D, # Frequency Block
        E = E, # InChI Length Block
        F = F, # UniChem Labels
        G = G, # Assignment Status
        H = 1, # Data Structure
    )
    response = requests.get(url)
    try:
        response = response.json()
    except ValueError:
        print('cannot decode json:', url)
        return
    if 'error' in response:
        print('UniChem error:', response['error'])
        return
    for assignment in response.values():
        header = assignment.pop(0)
        for match in assignment:
            yield collections.OrderedDict(zip(header, match))

def key_search(inchikey, **kwargs):
    """Search by InChIKeys."""
    if inchikey.startswith('InChIKey='):
        prefix, inchikey = inchikey.split('=', 1)
    base_url = 'https://www.ebi.ac.uk/unichem/rest/key_search'
    search_url = '{base_url}/{StandardInChIKey}'.format(
        base_url = base_url,
        StandardInChIKey = inchikey)
    return connectivity_query(search_url, **kwargs)
    
def cpd_search(source, compound_id, **kwargs):
    """Search by source-specific identifiers."""
    base_url = 'https://www.ebi.ac.uk/unichem/rest/cpd_search'
    search_url = '{base_url}/{src_compound_id}/{src_id}'.format(
        base_url = base_url,
        src_compound_id = compound_id,
        src_id = source_to_id[source])
    return connectivity_query(search_url, **kwargs)

In [7]:
#https://chembl.gitbook.io/unichem/api/sources
#https://www.ebi.ac.uk/unichem/search/connectivity
#https://www.ebi.ac.uk/unichem/search/connectivity?type=sourceID&compound=DB00006&sourceID=2
#https://www.ncbi.nlm.nih.gov/pmc/articles/PMC4158273/
def unichem_search(search_type, source, compound_id):
    url = "https://www.ebi.ac.uk/unichem/api/v1/connectivity"
    
    if search_type=='sourceID':
        payload = {
            "type": "sourceID",
            "compound": compound_id,
            "searchComponents": True,
            "sourceID": str(source_to_id[source])
        }
    elif search_type=='inchikey':
        payload = {
            "type": "inchikey",
            "compound": compound_id,
            "searchComponents": True
        }
    
    headers = {"Content-Type": "application/json"}

    response = requests.request("POST", url, json=payload, headers=headers)

    try:
        response = response.json() #json.dumps(response) 
    except ValueError:
        print('cannot decode json:', url)
        return
    if response['response'] == 'Not found':
        print('UniChem error:', search_type, response['response'])
        return
    
    return response['sources']

In [8]:
# mapping writer
mapping_path = os.path.join(path, 'mapping.tsv.gz')
mapping_file = gzip.open(mapping_path, 'wb')
mapping_buffer = io.TextIOWrapper(mapping_file, line_buffering = True)
mapping_fields = ['drugbank_id', 'drugbank_name', 'id', 'source_name', 'compoundId', 'baseIDURLAvailable', 'longName', 'shortName', 'typeOfSearch', 'url'
              ] #'C', 'Query_InChIKey', 'CpdId_InChIKey', 'Full_Query_InChI', 'Full_CpdId_InChI', 'Matching_Query_InChI', 'Matching_CpdId_InChI', 'b', 'i', 'm', 'p', 's', 't'
mapping_writer = csv.DictWriter(mapping_buffer, delimiter = '\t', fieldnames = mapping_fields, extrasaction = 'ignore')
mapping_writer.writeheader()

# mapping counts writer
count_path = os.path.join(path, 'mapping-counts.tsv')
count_file = open(count_path, 'w')
source_names = [id_to_source[i] for i in sorted(set(id_to_source) - {0})]
count_fields = ['drugbank_id', 'drugbank_name'] + source_names
count_writer = csv.DictWriter(count_file, delimiter = '\t', fieldnames = count_fields, restval = 0)
count_writer.writeheader()


for drug in drugbank:
    if drug['type'] != 'small molecule':
        continue
    if not drug['inchikey']:
        continue
    drugbank_id = drug['drugbank_id']
    drugbank_name = drug['name']
    print(drugbank_id, drugbank_name)
    query_matches = unichem_search('sourceID','drugbank', drugbank_id)
    if not query_matches:
        if drug['inchi'].startswith('InChI=1S'):
            query_matches = unichem_search('inchikey','drugbank', drug['inchikey'])
        else: 
            print('non-standard InChI: cannot query compound')
            continue
    #if query_matches is not None:
    #    continue
    query_matches = list(query_matches)
    #query_matches = list(cpd_search('drugbank', drugbank_id, C = 4))
    #    if drug['inchi'].startswith('InChI=1S'):
    #        query_matches = list(key_search(drug['inchikey'], C = 4))
    #    else: # non-standard InChI
    #        print('non-standard InChI: cannot query compound')
    #        continue
    
    for match in query_matches:
        if match['id']<=31:
            match['drugbank_id'] = drugbank_id
            match['drugbank_name'] = drugbank_name
            match['source_name'] = id_to_source[int(match['id'])]
            mapping_writer.writerow(match)
    
    source_to_matches = dict()
    for match in query_matches:
        if match['id']<=31:
            match['source_name'] = id_to_source[int(match['id'])]
            match_set = source_to_matches.setdefault(match['source_name'], set())
            match_set.add(match['compoundId'])
    count = {k: len(v) for k, v in source_to_matches.items()}
    count = collections.defaultdict(int, count)
    count['drugbank_id'] = drugbank_id
    count['drugbank_name'] = drugbank_name
    count_writer.writerow(count)

mapping_file.close()
count_file.close()

DB00006 Bivalirudin
DB00007 Leuprolide
DB00014 Goserelin
DB00027 Gramicidin D
DB00035 Desmopressin
DB00050 Cetrorelix
DB00067 Vasopressin
DB00080 Daptomycin
DB00091 Cyclosporine
DB00106 Abarelix
DB00114 Pyridoxal phosphate
DB00115 Cyanocobalamin
DB00116 Tetrahydrofolic acid
DB00117 Histidine
DB00118 Ademetionine
DB00119 Pyruvic acid
DB00120 Phenylalanine
DB00121 Biotin
DB00122 Choline
DB00123 Lysine
DB00125 Arginine
DB00126 Ascorbic acid
DB00127 Spermine
DB00128 Aspartic acid
DB00129 Ornithine
DB00130 L-Glutamine
DB00131 Adenosine phosphate
DB00132 alpha-Linolenic acid
DB00133 Serine
DB00134 Methionine
DB00135 Tyrosine
DB00136 Calcitriol
DB00137 Lutein
DB00138 Cystine
DB00139 Succinic acid
DB00140 Riboflavin
DB00141 N-Acetylglucosamine
DB00142 Glutamic acid
DB00143 Glutathione
DB00144 Phosphatidyl serine
DB00145 Glycine
DB00146 Calcifediol
DB00147 Pyridoxal
DB00148 Creatine
DB00149 Leucine
DB00150 Tryptophan
DB00151 Cysteine
DB00152 Thiamine
DB00153 Ergocalciferol
DB00154 Dihomo-gamma-

DB00519 Trandolapril
DB00520 Caspofungin
DB00521 Carteolol
DB00522 Bentiromide
DB00523 Alitretinoin
DB00524 Metolazone
DB00525 Tolnaftate
DB00526 Oxaliplatin
DB00527 Cinchocaine
DB00528 Lercanidipine
DB00529 Foscarnet
DB00530 Erlotinib
DB00531 Cyclophosphamide
DB00532 Mephenytoin
DB00533 Rofecoxib
DB00534 Chlormerodrin
DB00535 Cefdinir
DB00536 Guanidine
DB00537 Ciprofloxacin
DB00538 Gadoversetamide
DB00539 Toremifene
DB00540 Nortriptyline
DB00541 Vincristine
DB00542 Benazepril
DB00543 Amoxapine
DB00544 Fluorouracil
DB00545 Pyridostigmine
DB00546 Adinazolam
DB00547 Desoximetasone
DB00548 Azelaic acid
DB00549 Zafirlukast
DB00550 Propylthiouracil
DB00551 Acetohydroxamic acid
DB00552 Pentostatin
DB00553 Methoxsalen
DB00554 Piroxicam
DB00555 Lamotrigine
DB00556 Perflutren
DB00557 Hydroxyzine
DB00558 Zanamivir
DB00559 Bosentan
DB00560 Tigecycline
DB00561 Doxapram
DB00562 Benzthiazide
DB00563 Methotrexate
DB00564 Carbamazepine
DB00565 Cisatracurium
DB00566 Succimer
DB00567 Cephalexin
DB00568 

DB00931 Metacycline
DB00932 Tipranavir
DB00933 Mesoridazine
DB00934 Maprotiline
DB00935 Oxymetazoline
DB00936 Salicylic acid
DB00937 Diethylpropion
DB00938 Salmeterol
DB00939 Meclofenamic acid
DB00940 Methantheline
DB00941 Hexafluronium
DB00942 Cycrimine
DB00943 Zalcitabine
DB00944 Demecarium
DB00945 Acetylsalicylic acid
DB00946 Phenprocoumon
DB00947 Fulvestrant
DB00948 Mezlocillin
DB00949 Felbamate
DB00950 Fexofenadine
DB00951 Isoniazid
DB00952 Naratriptan
DB00953 Rizatriptan
DB00954 Dirithromycin
DB00955 Netilmicin
DB00956 Hydrocodone
DB00957 Norgestimate
DB00958 Carboplatin
DB00959 Methylprednisolone
DB00960 Pindolol
DB00961 Mepivacaine
DB00962 Zaleplon
DB00963 Bromfenac
DB00964 Apraclonidine
DB00966 Telmisartan
DB00967 Desloratadine
DB00968 Methyldopa
DB00969 Alosetron
DB00970 Dactinomycin
DB00971 Selenium Sulfide
DB00972 Azelastine
DB00973 Ezetimibe
DB00974 Edetic acid
DB00975 Dipyridamole
DB00976 Telithromycin
DB00977 Ethinylestradiol
DB00978 Lomefloxacin
DB00979 Cyclopentolate
D

DB01400 Neostigmine
DB01401 Choline magnesium trisalicylate
DB01403 Methotrimeprazine
DB01405 Temafloxacin
DB01406 Danazol
DB01407 Clenbuterol
DB01408 Bambuterol
DB01409 Tiotropium
DB01410 Ciclesonide
DB01411 Pranlukast
DB01412 Theobromine
DB01413 Cefepime
DB01414 Cefacetrile
DB01415 Ceftibuten
DB01416 Cefpodoxime
DB01418 Acenocoumarol
DB01419 Antrafenine
DB01420 Testosterone propionate
DB01421 Paromomycin
DB01422 Nitroxoline
DB01423 Stepronin
DB01424 Aminophenazone
DB01425 Alizapride
DB01426 Ajmaline
DB01427 Amrinone
DB01428 Oxybenzone
DB01429 Aprindine
DB01430 Almitrine
DB01431 Allylestrenol
DB01433 Methadyl acetate
DB01434 19-norandrostenedione
DB01435 Antipyrine
DB01436 Alfacalcidol
DB01437 Glutethimide
DB01438 Phenazopyridine
DB01439 3-Methylthiofentanyl
DB01440 gamma-Hydroxybutyric acid
DB01441 5-Methoxy-N,N-diisopropyltryptamine
DB01442 MMDA
DB01443 19-Nor-5-androstenedione
DB01444 Dimethylthiambutene
DB01445 Bufotenine
DB01446 Indopan
DB01447 4-Methylaminorex
DB01450 Dihydroeto

DB01718 Cetrimonium
DB01719 Thio-Maltopentaose
DB01720 (2Z)-2-(Benzoylamino)-3-[4-(2-bromophenoxy)phenyl]acrylic acid
DB01721 N-[2-hydroxy-1-indanyl]-5-[(2-tertiarybutylaminocarbonyl)-4(benzo[1,3]dioxol-5-ylmethyl)-piperazino]-4-hydroxy-2-(1-phenylethyl)-pentanamide
DB01723 {3-[3-(3,4-Dimethoxy-Phenyl)-1-(1-{1-[2-(3,4,5-Trimethoxy-Phenyl)-Butyryl]-Piperidin-2yl}-Vinyloxy)-Propyl]-Phenoxy}-Acetic Acid
DB01724 L-Threoninol
DB01725 2-{2-hydroxy-[1,1'-biphenyl]-3-yl}-1H-1,3-benzodiazole-5-carboximidamide
DB01726 2-Aminophenol
DB01727 Isocitric Acid
DB01728 1,2-dihexadecanoyl-sn-glycero-3-phosphoethanolamine
DB01729 1D-myo-inositol 1,3,4-trisphosphate
DB01731 (S)-wiskostatin
DB01732 (4R,5S,6S,7R)-1,3-dibenzyl-4,7-bis(phenoxymethyl)-5,6-dihydroxy-1,3 diazepan-2-one
DB01733 L-Phospholactate
DB01734 3-(Oxalyl-Amino)-Naphthalene-2-Carboxylic Acid
DB01735 3-Chloroalaninate
DB01736 [3-(Dodecanoylamino)Propyl](Hydroxy)Dimethylammonium
DB01737 Nalpha-(2-Naphthylsulfonylglycyl)-3-Amidino-D,L-Phenyla

...

DB08424 [5-AMINO-1-(4-FLUOROPHENYL)-1H-PYRAZOL-4-YL](3-{[(2R)-2,3-DIHYDROXYPROPYL]OXY}PHENYL)METHANONE
DB08426 THIENO[3,2-B]PYRIDINE-2-SULFONIC ACID [2-OXO-1-(1H-PYRROLO[2,3-C]PYRIDIN-2-YLMETHYL)-PYRROLIDIN-3-YL]-AMIDE
DB08427 Prephenic acid
DB08428 3(S)-AMINO-4-PHENYL-BUTAN-2(S)-OL
DB08429 N-({(2S)-1-[(3R)-3-amino-4-(3-chlorophenyl)butanoyl]pyrrolidin-2-yl}methyl)-3-(methylsulfonyl)benzamide
DB08430 PARA-NITROPHENYL 1-THIO-BETA-D-GLUCOPYRANOSIDE
DB08431 [(3R,4S)-4-HYDROXY-3-METHYL-2-OXOHEXYL]PHOSPHONIC ACID
DB08432 THYMIDINE-5'-THIOPHOSPHATE
DB08433 phenyl ethenesulfonate
DB08434 2-METHYLCARBAMOYL-3-(4-PHOSPHONOOXY-PHENYL)-CYCLOPROPANECARBOXYLIC ACID
DB08435 (5E,14E)-11-oxoprosta-5,9,12,14-tetraen-1-oic acid
DB08436 8-BENZO[1,3]DIOXOL-,5-YLMETHYL-9-BUTYL-9H-
DB08437 Puromycin
DB08438 (2E,4R,5S)-2,3,4,5-TETRAHYDROXY-6-(PALMITOYLOXY)HEX-2-ENOIC ACID
DB08439 Parecoxib
DB08440 N-1,10-phenanthrolin-5-ylacetamide
DB08441 6-BROMO-13-THIA-2,4,8,12,19-PENTAAZATRICYCLO[12.3.1.1~3,7~]NONADECA-1(

DB08541 [(3S)-9-hydroxy-1-methyl-10-oxo-4,10-dihydro-3H-benzo[g]isochromen-3-yl]acetic acid
DB08542 3,4-dihydroxy-9,10-secoandrosta-1(10),2,4-triene-9,17-dione
DB08543 1-[2-HYDROXY-3-(4-CYCLOHEXYL-PHENOXY)-PROPYL]-4-(2-PYRIDYL)-PIPERAZINE
DB08544 (S)-Fluoxetine
DB08545 (1S)-1-Phenylethyl (4-acetamidobenzyl)phosphonate
DB08546 4-[(3AS,4R,7R,8AS,8BR)-2-(1,3-BENZODIOXOL-5-YLMETHYL)-7-HYDROXY-1,3-DIOXODECAHYDROPYRROLO[3,4-A]PYRROLIZIN-4-YL]BENZENECARBOXIMIDAMIDE
DB08547 PROGESTERONE-11-ALPHA-OL-HEMISUCCINATE
DB08548 [(4S)-2,2-dimethyl-1,3-dioxolan-4-yl]methyl hydrogen hex-5-enylphosphonate
DB08549 (3R)-METHYLCARBAMOYL-7-SULFOAMINO-3,4-DIHYDRO-1H-ISOQUINOLINE-2-CARBOXYLIC ACID BENZYL ESTER
DB08550 7,8-Dichloro-1,2,3,4-tetrahydroisoquinoline
DB08551 3-{(R)-(Dihydroxyboryl)[(2-thienylacetyl)amino]methyl}benzoic acid
DB08552 (1R)-1-(2-thienylacetylamino)-1-phenylmethylboronic acid
DB08553 (1E)-5-(1-piperidin-4-yl-3-pyridin-4-yl-1H-pyrazol-4-yl)-2,3-dihydro-1H-inden-1-one oxime
DB08554 N-(3-car

DB08669 METHYL N-[(2S,3R)-3-AMINO-2-HYDROXY-3-(4-METHYLPHENYL)PROPANOYL]-D-ALANYL-D-LEUCINATE
DB08670 METHYL N-[(2S,3R)-3-AMINO-2-HYDROXY-3-(4-ISOPROPYLPHENYL)PROPANOYL]-D-ALANYL-D-LEUCINATE
DB08671 5-Imino-4-(2-trifluoromethyl-phenylazo)-5H-pyrazol-3-ylamine
DB08672 4-[(3R)-3-{[2-(4-FLUOROPHENYL)-2-OXOETHYL]AMINO}BUTYL]BENZAMIDE
DB08673 4-[(5-ISOPROPYL-1,3-THIAZOL-2-YL)AMINO]BENZENESULFONAMIDE
DB08674 (20S)-19,20,21,22-TETRAHYDRO-19-OXO-5H-18,20-ETHANO-12,14-ETHENO-6,10-METHENO-18H-BENZ[D]IMIDAZO[4,3-K][1,6,9,12]OXATRIAZA-CYCLOOCTADECOSINE-9-CARBONITRILE
DB08675 (5Z)-7-{(1R,4S,5R,6R)-6-[(1E)-1-Octen-1-yl]-2,3-diazabicyclo[2.2.1]hept-2-en-5-yl}-5-heptenoic acid
DB08676 (20S)-19,20,22,23-TETRAHYDRO-19-OXO-5H,21H-18,20-ETHANO-12,14-ETHENO-6,10-METHENOBENZ[D]IMIDAZO[4,3-L][1,6,9,13]OXATRIAZACYCLONOADECOSINE-9-CARBONITRILE
DB08677 N-(5-Isopropyl-thiazol-2-YL)-2-pyridin-3-YL-acetamide
DB08678 (4-ETHYLPHENYL)SULFAMIC ACID
DB08680 N-{3-[(E)-(tert-butoxyimino)methyl]-4-chlorophenyl}-2-methylfu

DB08782 4-(2-AMINOETHYL)BENZENESULFONAMIDE
DB08783 (4-{(2S)-2-[(tert-butoxycarbonyl)amino]-3-methoxy-3-oxopropyl}phenyl)methaneseleninic acid
DB08784 2-(4-CHLORO-PHENYLAMINO)-NICOTINIC ACID
DB08785 4-Methylcoumarin
DB08786 4-(2-methoxyethoxy)-6-methylpyrimidin-2-amine
DB08787 4-(2,4-dichlorophenyl)-5-phenyldiazenyl-pyrimidin-2-amine
DB08788 3,6-DIAMINO-5-CYANO-4-(4-ETHOXYPHENYL)THIENO[2,3-B]PYRIDINE-2-CARBOXAMIDE
DB08789 2-AMINO-4-(2,4-DICHLOROPHENYL)-N-ETHYLTHIENO[2,3-D]PYRIMIDINE-6-CARBOXAMIDE
DB08790 1-PHENYL-1H-PYRAZOLE-4-CARBOXYLIC ACID
DB08791 1-[(2-NITROPHENYL)SULFONYL]-1H-PYRROLO[3,2-B]PYRIDINE-6-CARBOXAMIDE
DB08792 Diloxanide
DB08794 Ethyl biscoumacetate
DB08795 Azidocillin
DB08796 Pipazethate
DB08797 Salicylamide
DB08798 Sulfamoxole
DB08799 Antazoline
DB08800 Chloropyramine
DB08801 Dimetindene
DB08802 Isothipendyl
DB08803 Tymazoline
DB08804 Nandrolone decanoate
DB08805 Metiamide
DB08806 Roxatidine acetate
DB08807 Bopindolol
DB08808 Bupranolol
DB08809 Dichloroacetic acid
DB088

ConnectionError: HTTPSConnectionPool(host='www.ebi.ac.uk', port=443): Max retries exceeded with url: /unichem/api/v1/connectivity (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x106b6ba90>: Failed to establish a new connection: [Errno 8] nodename nor servname provided, or not known'))

In [12]:
for drug in drugbank[8180:]:
    if drug['type'] != 'small molecule':
        continue
    if not drug['inchikey']:
        continue
    drugbank_id = drug['drugbank_id']
    drugbank_name = drug['name']
    print(drugbank_id, drugbank_name)
    query_matches = unichem_search('sourceID','drugbank', drugbank_id)
    if not query_matches:
        if drug['inchi'].startswith('InChI=1S'):
            query_matches = unichem_search('inchikey','drugbank', drug['inchikey'])
        else: 
            print('non-standard InChI: cannot query compound')
            continue
    #if query_matches is not None:
    #    continue
    query_matches = list(query_matches)
    #query_matches = list(cpd_search('drugbank', drugbank_id, C = 4))
    #    if drug['inchi'].startswith('InChI=1S'):
    #        query_matches = list(key_search(drug['inchikey'], C = 4))
    #    else: # non-standard InChI
    #        print('non-standard InChI: cannot query compound')
    #        continue
    
    for match in query_matches:
        if match['id']<=31:
            match['drugbank_id'] = drugbank_id
            match['drugbank_name'] = drugbank_name
            match['source_name'] = id_to_source[int(match['id'])]
            mapping_writer.writerow(match)
    
    source_to_matches = dict()
    for match in query_matches:
        if match['id']<=31:
            match['source_name'] = id_to_source[int(match['id'])]
            match_set = source_to_matches.setdefault(match['source_name'], set())
            match_set.add(match['compoundId'])
    count = {k: len(v) for k, v in source_to_matches.items()}
    count = collections.defaultdict(int, count)
    count['drugbank_id'] = drugbank_id
    count['drugbank_name'] = drugbank_name
    count_writer.writerow(count)

mapping_file.close()
count_file.close()

DB09164 Technetium Tc-99m disofenin
DB09165 Technetium Tc-99m pyrophosphate
DB09166 Etizolam
DB09167 Dosulepin
DB09168 4-Phenylfentanyl
DB09169 3-Allylfentanyl
DB09170 β-Hydroxythiofentanyl
DB09171 β-Methylfentanyl
DB09172 Brifentanil
DB09173 Butyrfentanyl
DB09174 Lofentanil
DB09175 Mirfentanil
DB09177 p-Fluorofentanyl
DB09178 Phenaridine
DB09179 R-30490
DB09180 Thienylfentanyl
DB09181 Trefentanil
DB09182 Benzylfentanyl
DB09183 Dasabuvir
DB09184 Edivoxetine
DB09185 Viloxazine
DB09186 Nisoxetine
DB09187 Lortalamine
DB09188 Amedalin
DB09189 Daledalin
DB09190 Talopram
DB09191 Talsupram
DB09192 Tandamine
DB09193 CP-39,332
DB09194 Etoperidone
DB09195 Lorpiprazole
DB09196 Lubazodone
DB09197 Mepiprazole
DB09198 Lobeglitazone
DB09199 Netoglitazone
DB09200 Rivoglitazone
DB09201 Ciglitazone
DB09202 Cirazoline
DB09203 Synephrine
DB09204 Arotinolol
DB09205 Moxisylyte
DB09206 Trimazosin
DB09207 AS-8112
DB09209 Pholcodine
DB09210 Piracetam
DB09211 Limaprost
DB09212 Loxoprofen
DB09213 Dexibuprofen
DB

DB11283 DL-dimyristoylphosphatidylcholine
DB11284 DL-dimyristoylphosphatidylglycerol
DB11285 Ethyl ferulate
DB11288 Borneol
DB11290 Aluminium tristearate
DB11291 2-ethylhexyl benzoate
DB11296 Prezatide
DB11297 Palmitoyl oligopeptide
DB11299 Vanillyl butyl ether
DB11304 Phenoxyethanol
DB11309 Sulfuric acid
DB11315 Methscopolamine
DB11318 1,2-Docosahexanoyl-sn-glycero-3-phosphoserine
DB11323 Glycol salicylate
DB11324 Nonivamide
DB11326 Boric acid
DB11327 Dipyrithione
DB11328 Tetradecyl hydrogen sulfate (ester)
DB11331 1-Palmitoyl-2-oleoyl-sn-glycero-3-(phospho-rac-(1-glycerol))
DB11332 Sinapultide
DB11335 Ascorbyl glucoside
DB11336 Kinetin
DB11337 Zeatin
DB11340 Ubiquinol
DB11342 Aluminum oxide
DB11343 Silanol
DB11344 (+)-menthol
DB11345 (S)-camphor
DB11346 Rubidium
DB11348 Calcium Phosphate
DB11349 Cetyl ethylhexanoate
DB11359 Guaiacol
DB11362 Selexipag
DB11363 Alectinib
DB11364 Pidotimod
DB11365 Sennosides
DB11366 Roquinimex
DB11367 Cefroxadine
DB11368 Chlorophetanol
DB11369 Afoxolaner

DB11837 Osilodrostat
DB11838 Revamilast
DB11839 PZ-128
DB11841 Entinostat
DB11843 PF-04958242
DB11844 Pritelivir
DB11845 Lucitanib
DB11846 Creatinine
DB11847 Cadazolid
DB11848 Mannose 6-phosphate
DB11851 Bafetinib
DB11852 Tegobuvir
DB11853 Relugolix
DB11855 Revefenacin
DB11858 Leukotriene D4
DB11859 Brexanolone
DB11860 Aramchol
DB11861 Litronesib
DB11863 Alvelestat
DB11864 Preladenant
DB11865 Brivanib alaninate
DB11867 JNJ-39393406
DB11868 Etiracetam
DB11869 Valspodar
DB11870 RG-4733
DB11871 PF-00610355
DB11872 ZD-6126
DB11873 Verinurad
DB11874 Crocin
DB11875 3,3'-diindolylmethane
DB11876 Alanyl glutamine
DB11877 Basmisanil
DB11878 Filibuvir
DB11879 Dusquetide
DB11880 Acridine Carboxamide
DB11881 AUY922
DB11882 BPC-157
DB11883 SB-705498
DB11885 Anlotinib
DB11886 Infigratinib
DB11888 Laninamivir octanoate
DB11889 Lanicemine
DB11890 Cilengitide
DB11891 Fimepinostat
DB11892 Prulifloxacin
DB11893 Avagacestat
DB11894 Efatutazone
DB11896 Gedatolisib
DB11898 2,4-thiazolidinedione
DB11899 MK-8

DB12343 Temocillin
DB12345 MBX-2982
DB12347 CG-400549
DB12348 5-amino-1,3,4-thiadiazole-2-thiol
DB12350 Rostafuroxin
DB12351 Siagoside
DB12352 Bizelesin
DB12353 Ulodesine
DB12354 Imrecoxib
DB12355 Netazepide
DB12357 BMS-863233
DB12358 Enbucrilate
DB12359 BIIB021
DB12360 PF-03654764
DB12361 Piclozotan
DB12362 Diaminopropanol tetraacetic acid
DB12364 Betrixaban
DB12365 Perzinfotel
DB12367 Selurampanel
DB12368 AZD-3839
DB12369 Sotrastaurin
DB12370 Ipamorelin
DB12371 Siponimod
DB12375 Oglemilast
DB12376 Ricolinostat
DB12377 Relebactam
DB12378 Apricoxib
DB12379 Indirubin
DB12380 GDC-0152
DB12381 Merestinib
DB12382 R-306465
DB12383 Cytochlor
DB12384 Silatecan
DB12385 10-hydroxycamptothecin
DB12387 OSI-027
DB12388 Evocalcet
DB12389 Zamicastat
DB12390 Seladelpar
DB12391 Sagopilone
DB12392 Resminostat
DB12393 Fanapanel
DB12394 Eleclazine
DB12395 Esreboxetine
DB12397 DSM-265
DB12398 Naproxen etemesil
DB12399 Polmacoxib
DB12400 Voxtalisib
DB12401 Bromperidol
DB12402 Pumosetrag
DB12403 Samarium
DB

DB12860 Actinium
DB12861 Rimeporide
DB12863 Sivelestat
DB12864 Melarsoprol
DB12865 Etelcalcetide
DB12866 Pradigastat
DB12867 Benperidol
DB12868 Intoplicine
DB12869 Eliprodil
DB12870 Buthionine sulfoximine
DB12873 Dianhydrogalactitol
DB12874 Quizartinib
DB12875 Mavatrep
DB12876 GS-9256
DB12877 Oxatomide
DB12878 AV-101
DB12879 Omigapil
DB12881 Indole-3-carbinol
DB12882 Ombrabulin
DB12883 Eltoprazine
DB12884 Lavoltidine
DB12885 Namodenoson
DB12886 GSK-1521498
DB12887 Tazemetostat
DB12888 Ezutromid
DB12889 Velneperit
DB12890 Dihydrexidine
DB12892 MGB-BP-3
DB12894 Raluridine
DB12895 Olitigaltin
DB12896 PSI-352938
DB12897 MK-7622
DB12899 TT-301
DB12900 Irdabisant
DB12901 Fiacitabine
DB12902 Trofosfamide
DB12903 DEBIO-1347
DB12904 ZSTK-474
DB12905 Samarium Sm-153
DB12906 LY-2334737
DB12907 Mannose
DB12910 Emicerfont
DB12911 Nicoboxil
DB12912 Nolatrexed
DB12914 Resmetirom
DB12916 Mitolactol
DB12919 T-62
DB12920 Pinometostat
DB12921 Chlorsulfaquinoxaline
DB12923 Gallopamil
DB12924 Ozenoxacin
DB

...

DB14986 Linrodostat
DB14987 Difamilast
DB14989 Umbralisib
DB14993 Pyrotinib
DB14995 NP-G2-044
DB14998 Olorinab
DB15003 PF-06700841
DB15006 Flufenoxuron
DB15008 GO-203-2C
DB15009 PF-04937319
DB15010 Edasalonexent
DB15011 Avacopan
DB15012 Farampator
DB15013 TAK-243
DB15016 Palladium Pd-103
DB15021 Leriglitazone
DB15023 BMS-791826
DB15024 Apararenone
DB15026 CXA-10
DB15027 Adriforant
DB15028 MK-1064
DB15029 AZD-8186
DB15031 Daridorexant
DB15033 Flortaucipir
DB15034 PRI-724
DB15035 Zanubrutinib
DB15036 Sitravatinib
DB15038 Litoxetine
DB15039 ITI-214
DB15040 TP-271
DB15041 Florilglutamic acid F-18
DB15046 LY-2881835
DB15047 BMS-919373
DB15048 Licogliflozin
DB15049 Sucralose
DB15050 Neopterin
DB15051 Ethaselen
DB15052 Ansofaxine
DB15054 TAS-117
DB15055 ABT-639
DB15056 Bifenthrin
DB15057 osgemcitabine palabenamide
DB15058 Flutemetamol
DB15059 Aprocitentan
DB15062 Inarigivir
DB15063 Inarigivir soproxil
DB15065 PF-06291874
DB15068 Agerafenib
DB15071 Omidenepag isopropyl
DB15073 Ribose
DB15075 4

DB15664 Vitamin K7
DB15665 SEP-363856
DB15666 Iodopropynyl butylcarbamate
DB15668 Silver oxide
DB15669 Fezolinetant
DB15670 Gusacitinib
DB15671 Besifovir
DB15672 Rilematovir
DB15673 Lenacapavir
DB15674 Sisunatovir
DB15675 Baloxavir
DB15678 Calcium undecylenate
DB15679 Aluminum subacetate
DB15684 2,3-dichloro-5,6-dicyanobenzoquinone
DB15685 Selpercatinib
DB15686 GS-441524
DB15687 Tridecactide
DB15688 Zavegepant
DB15690 Fluoroestradiol F-18
DB15694 Cedazuridine
DB15720 Zinc orotate
DB15759 Metronidazole benzoate
DB15760 Cobaltous sulfate
DB15761 Sulbactam pivoxil
DB15763 Iron polymaltose
DB15764 Benzyl nicotinate
DB15774 beta-Escin
DB15775 Algestone acetophenide
DB15777 Fluocortolone pivalate
DB15778 Hydrogen iodide
DB15779 Mebrofenin
DB15780 Mertiatide
DB15782 Cetyl palmitate
DB15783 Pargeverine
DB15784 Carmoterol
DB15785 Myrtecaine
DB15790 Mecloxamine
DB15791 MK-0668
DB15793 Zinc phenolsulfonate
DB15795 Adiphenine
DB15796 GC-376 free acid
DB15797 GC-373
DB15816 Calcium monoethylfumarat

DB16290 DAPTA
DB16291 Peretinoin
DB16292 Perfluorodecalin
DB16293 Pexiganan
DB16294 Pexmetinib
DB16295 HSK-3486
DB16296 IPI-549
DB16297 Florzolotau F-18
DB16299 Poseltinib
DB16300 Praliciguat
DB16301 Preimplantation factor
DB16302 BP-14979
DB16303 Gallium-68 PSMA
DB16304 TAK-653
DB16305 Xevinapant
DB16306 Racemetyrosine
DB16308 Revaprazan
DB16310 Rezafungin
DB16312 TNP-2092
DB16315 Rivenprost
DB16319 GSK-2981278
DB16320 Rovazolac
DB16321 S-777469
DB16323 Satoreotide tetraxetan
DB16324 Selgantolimod
DB16325 Selodenoson
DB16326 Sepiapterin
DB16330 Simurosertib
DB16331 Siremadlin
DB16332 Sodelglitazar
DB16333 Sonlicromanol
DB16335 Sulopenem etzadroxil
DB16338 Taniborbactam
DB16339 ABX-196
DB16340 Tetrafluoroborate
DB16343 Tropifexor
DB16344 Tulrampator
DB16345 Uracil C-13
DB16346 Veliflapon
DB16347 Velsecorat
DB16349 Vicagrel
DB16351 Volinanserin
DB16353 Razuprotafib
DB16354 Avasopasem manganese
DB16390 Mobocertinib
DB16397 Terevalefim
DB16400 Sibofimloc
DB16403 Isoquercitrin
DB16404 Carv

DB17235 Linperlisib
DB17237 PHI-101
DB17240 Avicin D
DB17247 Bisantrene
DB17255 Etoposide toniribate
DB17257 JS-K
DB17260 Minnelide free acid
DB17261 Flubrobenguane F18
DB17263 Caflanone
DB17264 TRX-E-002-1
DB17269 Cirtuvivint
DB17270 Ceclazepide
DB17273 Granaticin B
DB17277 CBP-501
DB17278 Lutetium Lu177 Edotreotide
DB17283 Chrysoeriol
DB17297 Enitociclib
DB17298 Disufenton
DB17299 p-Toluenesulfonamide
DB17300 Tyroserleutide
DB17304 Doranidazole
DB17306 Metavert
DB17308 Laurocapram
DB17309 Minnelide
DB17312 Dotamtate Pb-212
DB17342 Trimethyltetradecylammonium
DB17352 WT-1 A1
DB17379 (R)-Gossypol
DB17383 FN-1501
DB17384 Tinengotinib
DB17385 Lipotecan
DB17386 Xenon Xe-129
DB17390 Vinblastine N-oxide
DB17408 Borocaptate
DB17410 Vodudeutentan
DB17414 TK216
DB17418 Retinamidic acid
DB17419 S-3APG
DB17456 Dalpiciclib
DB17472 Pirtobrutinib
DB17490 NT-219
DB17493 Bioymifi
DB17499 GB1211
DB17503 PP-F11N lutetium Lu-177
DB17506 Etrumadenant
DB17507 COTI-2
DB17508 Hafnium oxide
DB17510 PXS-5505


DB18542 VB-312
DB18545 Tildacerfont
DB18564 YT-001
DB18573 1,​2-​Dioleoyl-​sn-​glycero-​3-​phospho-​L-​serine
DB18578 Brigimadlin
DB18588 Denatonium
DB18600 DM-1157
DB18603 APPD
DB18632 1-(3-fluoro-4-(7-(5-methyl-1H-imidazol-2-yl)-1-oxo-2,3-dihydro-1H-isoindo-1-4-yl)-phenyl)-3-(3-trifluoromethyl-phenyl)-urea
DB18633 Uttroside B
DB18634 Vasoactive intestinal peptide
DB18657 PARPI F-18
DB18665 Psoralen
DB18689 GDP-L-fucose
DB18706 Emraclidine
DB18707 AVL-3288
DB18708 Alogabat
DB18709 Ropsacitinib
DB18711 taletrectinib
DB18715 Tolebrutinib
UniChem error: sourceID Not found
DB18716 Enmetazobactam
UniChem error: sourceID Not found


In [13]:
# write source-specific mapping files
mapping_path = os.path.join(path, 'mapping.tsv.gz')
mapping_file = gzip.open(mapping_path, 'rb')
mapping_buffer = io.TextIOWrapper(mapping_file)
reader = csv.DictReader(mapping_buffer, delimiter='\t')
source_to_pairs = dict()
for row in reader:
    pair = row['drugbank_id'], row['compoundId']
    pairs = source_to_pairs.setdefault(row['source_name'], set())
    pairs.add(pair)
mapping_file.close()

del source_to_pairs['drugbank']
for source, pairs in source_to_pairs.items():
    bindingdb_path = os.path.join(path, 'mapping', '{}.tsv'.format(source))
    write_file = open(bindingdb_path, 'w')
    writer = csv.writer(write_file, delimiter='\t')
    writer.writerow(['drugbank_id', '{}_id'.format(source)])
    writer.writerows(sorted(pairs))
    write_file.close()

In [15]:
import pandas

drugs =['DB00289','DB00669','DB00862','DB00977','DB01248','DB08801']
mapping_tsv_df = pandas.read_table('../data/DrugBank/mapping.tsv.gz')
mapping_tsv_df[mapping_tsv_df['drugbank_id'].isin(drugs)]

drugbank_id drugbank_name  id source_name     compoundId  \
19186      DB00289   Atomoxetine   1      chembl      CHEMBL641   
19187      DB00289   Atomoxetine   1      chembl   CHEMBL299052   
19188      DB00289   Atomoxetine   1      chembl  CHEMBL1442868   
19189      DB00289   Atomoxetine   2    drugbank        DB00289   
19190      DB00289   Atomoxetine   4      iuphar           7118   
...            ...           ...  ..         ...            ...   
286794     DB08801   Dimetindene  29     nikkaji        J8.041A   
286795     DB08801   Dimetindene  29     nikkaji      J541.230G   
286796     DB08801   Dimetindene  31   bindingdb       50297307   
286797     DB08801   Dimetindene  31   bindingdb          81452   
286798     DB08801   Dimetindene  31   bindingdb       50474485   

        baseIDURLAvailable               longName  shortName typeOfSearch  \
19186                 True                 ChEMBL     chembl        match   
19187                 True                 ChEMBL     chembl        match   
19188                 True                 ChEMBL     chembl        match   
19189                 True               DrugBank   drugbank        match   
19190                 True  Guide to Pharmacology     gtopdb        match   
...                    ...                    ...        ...          ...   
286794                True                Nikkaji    nikkaji        match   
286795                True                Nikkaji    nikkaji        match   
286796                True              BindingDB  bindingdb        match   
286797                True              BindingDB  bindingdb        match   
286798                True              BindingDB  bindingdb        match   

                                                      url  
19186   https://www.ebi.ac.uk/chembldb/compound/inspec...  
19187   https://www.ebi.ac.uk/chembldb/compound/inspec...  
19188   https://www.ebi.ac.uk/chembldb/compound/inspec...  
19189                http://www.drugbank.ca/drugs/DB00289  
19190   http://www.guidetopharmacology.org/GRAC/Ligand...  
...                                                   ...  
286794  http://jglobal.jst.go.jp/en/redirect?Nikkaji_N...  
286795  http://jglobal.jst.go.jp/en/redirect?Nikkaji_N...  
286796  http://www.bindingdb.org/bind/chemsearch/marvi...  
286797  http://www.bindingdb.org/bind/chemsearch/marvi...  
286798  http://www.bindingdb.org/bind/chemsearch/marvi...  

[1507 rows x 10 columns]

In [16]:
# check if they are in mapping tsv 8513+6 = 8519
bindingdb_id_df = pandas.read_table('../data/DrugBank/mapping/bindingdb.tsv')
bindingdb_id_df.shape
bindingdb_id_df[bindingdb_id_df['drugbank_id'].isin(drugs)]

drugbank_id  bindingdb_id
290      DB00289      50022784
291      DB00289      50366567
822      DB00669      50005835
1080     DB00862         14776
1081     DB00862      50088373
1082     DB00862      50111900
1246     DB00977        158504
1247     DB00977      50187243
1640     DB01248         36351
6075     DB08801      50297307
6076     DB08801      50474485
6077     DB08801         81452

In [17]:
bindingdb_id_df.shape

(9265, 2)

## Parse the BindingDB tsv export

This section peforms the following processing steps on the [BindingDB](http://www.bindingdb.org/bind/index.jsp) export:

+ processes affinities to floats
+ converts to entrez genes
+ simplifies observation into essential fields

See the corresponding [Thinklab discussion](http://doi.org/10.15363/thinklab.d53) for more information.

In [ ]:
import os
import csv
import gzip
import pprint
import collections
import operator

import pandas
import requests
import zipfile
from zipfile import ZipFile

In [ ]:
# uniprot to entrez gene mapping
url = '../data/UniProt/GeneID.tsv.gz'
uniprot_df = pandas.read_table(url, compression='gzip')

uniprot_to_entrez = dict()
for uniprot, entrez in zip(uniprot_df.uniprot, uniprot_df.GeneID):
    uniprot_to_entrez.setdefault(uniprot, set()).add(str(entrez))

In [ ]:
# Read and process BindingDB tsv
path ='../data/BindingDB/BindingDB_All_202405.tsv'
df = pandas.read_table(path, delimiter='\t', on_bad_lines='skip')

In [ ]:
#Field documentation: https://www.bindingdb.org/bind/chemsearch/marvin/BindingDB-TSV-Format.pdf

target_fields = [
    'BindingDB Target Chain  Sequence',
    'PDB ID(s) of Target Chain',
    'UniProt (SwissProt) Recommended Name of Target Chain',
    'UniProt (SwissProt) Entry Name of Target Chain',
    'UniProt (SwissProt) Primary ID of Target Chain',
    'UniProt (SwissProt) Secondary ID(s) of Target Chain',
    'UniProt (SwissProt) Alternative ID(s) of Target Chain',
    'UniProt (TrEMBL) Submitted Name of Target Chain',
    'UniProt (TrEMBL) Entry Name of Target Chain',
    'UniProt (TrEMBL) Primary ID of Target Chain',
    'UniProt (TrEMBL) Secondary ID(s) of Target Chain',
    'UniProt (TrEMBL) Alternative ID(s) of Target Chain',
]

chains_key = 'Number of Protein Chains in Target (>1 implies a multichain complex)'


chains_index = df.columns.get_loc(chains_key)
target0_index = chains_index + 1
ligand_fields = df.columns[:chains_index + 1]

verbose=True
max_rows=None

row_out = list()
for j, row in df.iterrows():
    if max_rows is not None and j == max_rows:
            break
    #row = [x if x else None for x in row] #do we need it?
    ligand_values = row[:chains_index + 1]
    # Ensure line has sufficient ligand fields
    if len(row) < chains_index + 1:
        if verbose:
            print('Line', j + 2, 'is deficient')
        continue
    rowdict = collections.OrderedDict(zip(ligand_fields, ligand_values))
    for key in [chains_key]:
        if key not in rowdict:
            print(j+2)
            print(row)
            print(rowdict)
        rowdict[key] = int(rowdict[key])
    chains = list()
    target_chain_cols = [col for col in df.columns if 'BindingDB Target Chain Sequence' in col]
    assert rowdict[chains_key] == (len(row[target_chain_cols])-len([i for i in row[target_chain_cols] if pandas.isnull(i) == True]))
    #assert rowdict[chains_key] == len(row[target0_index:]) / len(target_fields)
    for i in range(rowdict[chains_key]):
        i_0 = target0_index + i * len(target_fields)
        i_1 = target0_index + (i + 1) * len(target_fields)
        target_values = row[i_0:i_1]
        chain = collections.OrderedDict(zip(target_fields, target_values))
        chains.append(chain)
    rowdict['chains'] = chains
    row_out.append(rowdict)
row_out

In [ ]:
bindingdb_generator = row_out #read_bindingdb(path, verbose=True)

bindings = list()
for i, row in enumerate(bindingdb_generator):
    #if i > 10000:
    #    break
    if len(row['chains']) != 1:
        continue
    chain, = row['chains']
    uniprots = chain['UniProt (SwissProt) Primary ID of Target Chain']
    if pandas.isnull(uniprots) == True:
        continue #skip to another iteration of for loop
    uniprots = uniprots.split(',')

    template = dict()
    template['bindingdb_id'] = row['BindingDB MonomerID']
    template['reaction_id'] = row['BindingDB Reactant_set_id']
    template['source'] = row['Curation/DataSource']
    template['organism'] = row['Target Source Organism According to Curator or DataSource']
    template['pubmed'] = row['PMID']
    template['doi'] = row['Article DOI']

    affinities = {'Ki': row['Ki (nM)'], 'Kd': row['Kd (nM)'], 'IC50': row['IC50 (nM)']}
    for measure, affinity in affinities.items():
        if affinity is None:
            continue
        for uniprot in uniprots:
            entrez_set = uniprot_to_entrez.get(uniprot)
            if not entrez_set:
                # uniprot_id not found in mapping
                continue
            for entrez in entrez_set:
                binding = template.copy()
                binding['measure'] = measure
                binding['affinity_nM'] = affinity
                binding['uniprot'] = uniprot
                binding['entrez_gene'] = entrez
                bindings.append(binding)

In [ ]:
# Convert affinities to floats
lt, gt, eq, err = 0, 0, 0, 0
for binding in bindings:
    affinity = binding['affinity_nM']
    if str(affinity).startswith('<'):
        affinity = affinity.lstrip('<')
        affinity = float(affinity)
        if affinity >= 10.0:
            affinity -= 1.0
        lt += 1
    elif str(affinity).startswith('>'):
        affinity = affinity.lstrip('>')
        affinity = float(affinity)
        affinity += 1.0
        gt += 1
    else:
        try:
            affinity = float(affinity)
            eq += 1
        except ValueError:
            affinity = None
            err += 1
    binding['affinity_nM'] = affinity
print('< {}\n> {}\n= {}\nerrors {}'.format(lt, gt, eq, err))

In [ ]:
fields = ['reaction_id', 'bindingdb_id', 'uniprot', 'entrez_gene',
          'measure', 'affinity_nM', 'source', 'organism', 'pubmed', 'doi']
with gzip.open('../data/BindingDB/binding.tsv.gz', 'wt') as write_file:
    writer = csv.DictWriter(write_file, delimiter='\t', fieldnames=fields)
    writer.writeheader()
    bindings.sort(key=operator.itemgetter(*fields))
    writer.writerows(bindings)

## Collapsing bindingDB compound-gene relationships
run collapse.Rmd

## Create a single dataset of Compound-Gene binding relationships from BindingDB and DrugBank

In [18]:
import sys
import itertools

import pandas

In [19]:
def split_and_clean_ids(id_str, sep='|'):
    """Return a set of unique non-empty IDs from a joined string."""
    if not id_str or pandas.isnull(id_str):
        return set()
    id_set = set(id_str.split(sep))
    id_set.discard('')
    return id_set

### Read datasets

In [20]:
# Read DrugCentral
url = '../data/DrugCentral/targets.tsv'
central_df = pandas.read_table(url, dtype={'pubmed_ids': str})
for column in 'pubmed_ids', 'sources', 'actions', 'urls':
    central_df[column] = central_df[column].map(split_and_clean_ids)
central_df = central_df.rename(columns={'GeneID': 'entrez_gene_id'})
central_df.head(2)

entrez_gene_id drugbank_id drugbank_name pubmed_ids  \
0              18     DB01080    Vigabatrin         {}   
1              19     DB01599      Probucol         {}   

                  sources      actions urls  
0  {DrugCentral (ChEMBL)}  {inhibitor}   {}  
1  {DrugCentral (ChEMBL)}  {inhibitor}   {}

In [21]:
# Read BindingDB
url = '../data/BindingDB/bindings-drugbank-gene.tsv'
binding_df = pandas.read_table(url)
# Filter for micromolar binding affinity
binding_df = binding_df[binding_df.affinity_nM <= 1000]
# Parse compound fields
binding_df.sources = binding_df.sources.map(lambda x: split_and_clean_ids(x, ','))
binding_df.pubmeds = binding_df.pubmeds.map(lambda x: split_and_clean_ids(x, ','))
binding_df = binding_df.rename(columns={'entrez_gene': 'entrez_gene_id', 'pubmeds': 'pubmed_ids'})
binding_df.head(2)

drugbank_id  entrez_gene_id  affinity_nM  n_pairs   sources pubmed_ids  \
11     DB00091            2280         20.0        1  {ChEMBL}  {9857082}   
12     DB00091            2281          6.0        1  {ChEMBL}  {7473543}   

   drugbank_name  drugbank_approved gene_symbol  
11  Cyclosporine                  1      FKBP1A  
12  Cyclosporine                  1      FKBP1B

In [22]:
# Read DrubBank compound-gene interaction
url = '../data/DrugBank/proteins.tsv'
drugbank_protein_df = pandas.read_table(url)
drugbank_protein_df.pubmed_ids = drugbank_protein_df.pubmed_ids.map(
    lambda x: split_and_clean_ids(x, '|'))
drugbank_protein_df.actions = drugbank_protein_df.actions.map(
    lambda x: split_and_clean_ids(x, '|'))
drugbank_protein_df['sources'] = drugbank_protein_df.apply(
    lambda x: set(['DrugBank ({})'.format(x['category'])]), axis=1)
drugbank_protein_df.head(2)

drugbank_id category uniprot_id  entrez_gene_id organism known_action  \
0     DB00001   target     P00734            2147   Humans          yes   
1     DB00006   target     P00734            2147   Humans          yes   

       actions                                         pubmed_ids  \
0  {inhibitor}  {11467439, 10912644, 11055889, 11807012, 10505...   
1  {inhibitor}  {11929334, 11060732, 11504570, 11923794, 11752...   

               sources  
0  {DrugBank (target)}  
1  {DrugBank (target)}

In [23]:
# DrugBank gene-protein interactions by category
drugbank_protein_df.category.value_counts()

target         17192
enzyme          5866
transporter     3430
carrier          903
Name: category, dtype: int64

### Combine BindingDB and DrugBank

In [24]:
# Create a combined dataset of BindingDB and DrugBank by appending all rows
long_df = pandas.concat([
    central_df[['drugbank_id', 'entrez_gene_id', 'sources', 'pubmed_ids', 'actions', 'urls']],
    drugbank_protein_df[['drugbank_id', 'entrez_gene_id', 'sources', 'pubmed_ids', 'actions']],
    binding_df[['drugbank_id', 'entrez_gene_id', 'affinity_nM', 'sources', 'pubmed_ids']],
])

for column in 'pubmed_ids', 'actions', 'urls':
    long_df[column] = long_df[column].map(lambda x: x if pandas.notnull(x) else set())
long_df.head(2)

drugbank_id  entrez_gene_id                 sources pubmed_ids      actions  \
0     DB01080              18  {DrugCentral (ChEMBL)}         {}  {inhibitor}   
1     DB01599              19  {DrugCentral (ChEMBL)}         {}  {inhibitor}   

  urls  affinity_nM  
0   {}          NaN  
1   {}          NaN

In [25]:
def get_license(sources):
    """Return the license of a binding relationship based on its sources."""
    sources = frozenset(sources)
    if 'ChEMBL' in sources:
        return 'CC BY-SA 3.0'
    if any(x.startswith('DrugBank') for x in sources):
        return 'CC BY-NC 4.0'
    if 'BindingDB' in sources:
        return 'CC BY 3.0'
    if any(x.startswith('DrugCentral') for x in sources):
        return 'CC BY 4.0'
    return None

def condense(df):
    """Combine gene-compound relationships"""
    row = pandas.Series()
    row['sources'] = set(itertools.chain.from_iterable(df.sources))
    row['pubmed_ids'] = set(itertools.chain.from_iterable(df.pubmed_ids))
    row['actions'] = set(itertools.chain.from_iterable(df.actions))
    row['affinity_nM'] = df.affinity_nM.mean(skipna=True)
    row['license'] = get_license(row['sources'])
    row['urls'] = set(itertools.chain.from_iterable(df.urls))
    return row

condensed_df = long_df.groupby(['drugbank_id', 'entrez_gene_id']).apply(condense).reset_index()

/var/folders/sg/983t9lp12bsfyjv9ylh6002m0000gt/T/ipykernel_2561/2015764311.py:16: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  row = pandas.Series()
/var/folders/sg/983t9lp12bsfyjv9ylh6002m0000gt/T/ipykernel_2561/2015764311.py:16: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  row = pandas.Series()
/var/folders/sg/983t9lp12bsfyjv9ylh6002m0000gt/T/ipykernel_2561/2015764311.py:16: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  row = pandas.Series()
/var/folders/sg/983t9lp12bsfyjv9ylh6002m0000gt/T/ipykernel_2561/2015764311.py:16: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [26]:
# Number of condensed bindings
len(condensed_df)

46573

In [27]:
# Convert compound fields into pipe-delimited strings
for column in 'sources', 'pubmed_ids', 'actions', 'urls':
    condensed_df[column] = condensed_df[column].map(lambda x: '|'.join(sorted(x)))

In [28]:
# Save condensed bindings
condensed_df.to_csv('../data/BindingDB/CbG-binding.tsv', sep='\t', index=False)

In [29]:
condensed_df.head(2)

drugbank_id  entrez_gene_id            sources  \
0     DB00001            2147  DrugBank (target)   
1     DB00002             712  DrugBank (target)   

                                     pubmed_ids    actions  affinity_nM  \
0  10505536|10912644|11055889|11467439|11807012  inhibitor          NaN   
1                                      32117299     binder          NaN   

        license urls  
0  CC BY-NC 4.0       
1  CC BY-NC 4.0

## Compound bindings

In [30]:
import pandas
url = '../data/DrugBank/drugbank-slim.tsv'
compound_df = pandas.read_table(url)
compound_df.head(2)

drugbank_id         name            type                    groups  \
0     DB00006  Bivalirudin  small molecule  approved|investigational   
1     DB00007   Leuprolide  small molecule  approved|investigational   

         atc_codes                                         categories  \
0          B01AE06  Amino Acids, Peptides, and Proteins|Anticoagul...   
1  L02AE51|L02AE02  Adrenal Cortex Hormones|Agents Causing Muscle ...   

                      inchikey  \
0  OIRCOABEOLEUMC-GEJPAHFPSA-N   
1  GFIJNRVAKGFPGQ-LIJARHBVSA-N   

                                               inchi  \
0  InChI=1S/C98H138N24O33/c1-5-52(4)82(96(153)122...   
1  InChI=1S/C59H84N16O12/c1-6-63-57(86)48-14-10-2...   

                                         description  
0  Bivalirudin is a synthetic 20 residue peptide ...  
1  Leuprolide is a synthetic 9-residue peptide an...

In [31]:
url = '../data/EntrezGene/genes-human.tsv'
gene_df = pandas.read_table(url)
gene_df = gene_df[gene_df.type_of_gene == 'protein-coding']
coding_genes = set(gene_df.GeneID)

In [35]:
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

In [36]:
binding_df = pandas.read_table('../data/BindingDB/CbG-binding.tsv')
binding_df.shape
binding_df = binding_df.merge(compound_df[['drugbank_id']])
binding_df = binding_df[binding_df.entrez_gene_id.isin(coding_genes)]
binding_df.shape
binding_df.head(2)

(46573, 8)

(25733, 8)

drugbank_id  entrez_gene_id                                 sources  \
0     DB00006            2147  DrugBank (target)|DrugCentral (IUPHAR)   
1     DB00006            4353                       DrugBank (enzyme)   

                                          pubmed_ids    actions  affinity_nM  \
0  11060732|11504570|11752352|11833835|11923794|1...  inhibitor          NaN   
1                                           18701766  inhibitor          NaN   

        license urls  
0  CC BY-NC 4.0  NaN  
1  CC BY-NC 4.0  NaN